# ライブラリのインポート

In [1]:
import numpy as np
import utils as ut
import torch.nn as nn
import torch.nn.functional as F
import torch
import torchvision.models as models

# Discriminator

In [223]:
class Discriminator(nn.Module):
    
    def __init__(self, item_num, user_num, emb_dim,
                           lamda, param=None, initdelta=0.05):
        super(Discriminator, self).__init__()
        self.item_num = item_num
        self.user_num = user_num
        self.emb_dim = emb_dim
        self.lamda = lamda
        self.param = param
        self.initdelta = initdelta
        self.d_params = []
        
        if self.param is None:
            self.user_embeddings = nn.Embedding(
                self.user_num, self.emb_dim)            
            self.item_embeddings = nn.Embedding(
                self.item_num, self.emb_dim)            
            self.item_bias = nn.Embedding(
                self.item_num, 1)
            
            # initialize
            torch.nn.init.uniform_(
                self.user_embeddings.weight, a=initdelta, b=-initdelta)
            torch.nn.init.uniform_(
                self.item_embeddings.weight, a=initdelta, b=-initdelta)
#             torch.nn.init.uniform_(
#                 self.item_bias.weight, a=initdelta, b=-initdelta)
            
    def forward(self, user, item, label):
        pre_logits = (self.user_embeddings(user) * self.item_embeddings(item)).squeeze().sum(1).view(-1,1) + self.item_bias(item).view(-1, 1)
        pre_loss =  F.binary_cross_entropy_with_logits(pre_logits, label)
        return pre_loss

    def all_rating(self, user):
        all_rating = torch.mm(self.user_embeddings(user),
                                               self.item_embeddings.t()) + self.item_bias
        return all_rating

    def all_logits(self, user):
        all_logits = (self.user_embeddings(user) \
                              * self.item_embeddings).sum(1) + self.item_bias
        return all_logits

    def get_reward(self, user, item):
        reward_logits = (self.user_embeddings(user) \
                                     * self.item_embeddings(item).t()).sum(1) + self.item_bias(item)
        reward = 2 * (torch.nn.Sigmoid(reward_logits) - 0.5)
        return reward

# Generator

In [217]:
class Generator(nn.Module):
    
    def __init__(self, item_num, user_num, emb_dim,
                           lamda, param=None, initdelta=0.05, lr=0.05):
        super(Generator, self).__init__()
        self.item_num = item_num
        self.user_num = user_num
        self.emb_dim = emb_dim
        self.lamda = lamda
        self.param = param
        self.initdelta = initdelta
        self.lr = lr
        self.g_params = []
        
        if self.param is None:
            self.user_embeddings = nn.Embedding(
                self.user_num, self.emb_dim)
            self.item_embeddings = nn.Embedding(
                self.item_num, self.emb_dim)
            self.item_bias = torch.zeros(self.item_num) # (self.item_num)
            
            # initialize
            torch.nn.init.uniform_(
                self.user_embeddings.weight, a=initdelta, b=-initdelta)
            torch.nn.init.uniform_(
                self.item_embeddings.weight, a=initdelta, b=-initdelta)
        
    def forward(self, user, item, label, reward):
        i_prob = torch.gather(F.softmax(self.all_logits(user).view(1, -1), -1), item)
        loss = - (torch.log(i_prob) * reward).sum(1) \
                   + self.lamda * (F.normalize(self.user_embeddings(user), p=2, dim=1) \
                                             + F.normalize(self.item_embeddings(item), p=2, dim=1) \
                                             + F.normalize(self.item_bias(item), p=2, dim=1))
        return loss

    def all_rating(self, user):
        rating = torch.mm(self.user_embeddings(user).view(1, -1),
                                               self.item_embeddings.weight.t()) + self.item_bias
        return rating

    def all_logits(self, user):
        logits = (self.user_embeddings(user) \
                              * self.item_embeddings).sum(1) + self.item_bias
        return logits

# 評価関数

In [210]:
def dcg_at_k(r, k):
    r = np.asfarray(r)[:k]
    return np.sum(r / np.log2(np.arange(2, r.size + 2)))


def ndcg_at_k(r, k):
    dcg_max = dcg_at_k(sorted(r, reverse=True), k)
    if not dcg_max:
        return 0.
    return dcg_at_k(r, k) / dcg_max

def simple_test_one_user(x):
    # import pdb; pdb.set_trace()
    rating = x[0]
    u = x[1]

    test_items = list(all_items - set(user_pos_train[u]))
    item_score = []
    for i in test_items:
        item_score.append((i, rating[i]))

    item_score = sorted(item_score, key=lambda x: x[1])
    item_score.reverse()
    item_sort = [x[0] for x in item_score]

    r = []
    for i in item_sort:
        if i in user_pos_test[u]:
            r.append(1)
        else:
            r.append(0)

    p_3 = np.mean(r[:3])
    p_5 = np.mean(r[:5])
    p_10 = np.mean(r[:10])
    ndcg_3 = ndcg_at_k(r, 3)
    ndcg_5 = ndcg_at_k(r, 5)
    ndcg_10 = ndcg_at_k(r, 10)

    return np.array([p_3, p_5, p_10, ndcg_3, ndcg_5, ndcg_10])

def simple_test(model):
    result = np.array([0.] * 6)
    pool = multiprocessing.Pool(cores)
    batch_size = 128
    test_users = list(user_pos_test.keys())
    test_user_num = len(test_users)
    index = 0
    while True:
        if index >= test_user_num:
            break
        user_batch = test_users[index:index + batch_size]
        index += batch_size

        user_batch_rating = generator.module.all_rating(user_batch)
        user_batch_rating = user_batch_rating.detach_().cpu().numpy()

        user_batch_rating_uid = zip(user_batch_rating, user_batch)
        batch_result = pool.map(simple_test_one_user, user_batch_rating_uid)
        for re in batch_result:
            result += re

    pool.close()
    ret = result / test_user_num
    ret = list(ret)
    return ret

# ハイパーパラメーター

In [211]:
EMB_DIM = 5
USER_NUM = 943
ITEM_NUM = 1683
BATCH_SIZE = 16
INIT_DELTA = 0.05

all_items = set(range(ITEM_NUM))
workdir = "ml-100k/"
DIS_TRAIN_FILE = workdir + "dis-train.txt"

# ロードデータ

In [212]:
# positiveな要素だけを引っ張ってくる
user_pos_train = {}
with open(workdir + 'movielens-100k-train.txt')as fin:
    for line in fin:
        line = line.split()
        uid = int(line[0])
        iid = int(line[1])
        r = float(line[2])
        if r > 3.99:
            if uid in user_pos_train:
                user_pos_train[uid].append(iid)
            else:
                user_pos_train[uid] = [iid]

# testでnegativeな要素だけを引っ張ってくる                
user_pos_test = {}
with open(workdir + 'movielens-100k-test.txt')as fin:
    for line in fin:
        line = line.split()
        uid = int(line[0])
        iid = int(line[1])
        r = float(line[2])
        if r > 3.99:
            if uid in user_pos_test:
                user_pos_test[uid].append(iid)
            else:
                user_pos_test[uid] = [iid]

all_users = user_pos_train.keys()

# Generatorによるデータセレクト

In [213]:
def generate_for_d(model, filename):
    data = []
    for user in user_pos_train:
        pos = user_pos_train[user]

        rating = model.all_rating(torch.tensor(user))
        rating = rating.detach_().cpu().numpy()
        rating = np.array(rating[0]) / 0.2  # Temperature
        exp_rating = np.exp(rating)
        prob = exp_rating / np.sum(exp_rating)

        neg = np.random.choice(np.arange(ITEM_NUM), size=len(pos), p=prob)
        for i in range(len(pos)):
            data.append(str(user) + '\t' + str(pos[i]) + '\t' + str(neg[i]))

    with open(filename, 'w')as fout:
        fout.write('\n'.join(data))

In [224]:
generator = Generator(
    ITEM_NUM, USER_NUM,EMB_DIM, lamda=0.0 / BATCH_SIZE,
    param=None, initdelta=INIT_DELTA)

discriminator = Discriminator(
    ITEM_NUM, USER_NUM,EMB_DIM, lamda=0.0 / BATCH_SIZE,
    param=None, initdelta=INIT_DELTA)

g_optimizer = torch.optim.SGD(
    generator.parameters(), lr=0.001, momentum=0.9)

d_optimizer = torch.optim.SGD(
    discriminator.parameters(), lr=0.001, momentum=0.9)                    

In [225]:
from torch import nn
from torch import autograd

generator.train()
discriminator.train()
for epoch in range(15):
    if epoch >= 0:
        for d_epoch in range(100):
            if d_epoch % 5 == 0:
                generate_for_d(generator, DIS_TRAIN_FILE)
                train_size = ut.file_len(DIS_TRAIN_FILE)
            index = 1
            while True:
                if index > train_size:
                    break
                if index + BATCH_SIZE <= train_size + 1:
                    users, items, labels = ut.get_batch_data(
                        DIS_TRAIN_FILE, index, BATCH_SIZE)
                else:
                    users, items, labels = ut.get_batch_data(
                        DIS_TRAIN_FILE, index, train_size - index + 1)
                    
                users = torch.tensor(users).view(-1, 1)
                items = torch.tensor(items).view(-1, 1)
                labels = torch.tensor(labels).view(-1, 1)
    
                loss_d = discriminator(users, items, labels)
                d_optimizer.zero_grad()
                loss_d.backward()
                d_optimizer.step()
                print(loss_d)

#         for g_epoch in range(50):
#             for user in user_pos_train:
#                 sample_lambda = 0.2
#                 pos = user_pos_train[user]

#                 rating = generator.all_logits(user)
#                 exp_rating = np.exp(rating)
#                 prob = exp_rating / np.sum(exp_rating)

#                 pn = (1 - sample_lambda) + prob
#                 pn[pos] += sample_lambda * 1.0 / len(pos)

#                 sample = np.random.choice(np.range(ITEM_NUM), 2*len(pos), p=pn)
#                 reward = discriminator.get_reward(user, sample)
#                 reward = reward * prob[sample] / pn[sample]

# #                     users = # userを複数に
#                 loss_g = generator(user, sample, "label", reward)
#                 g_optimizer.zero_grad()
#                 loss_g.backward()
#                 g_optimizer.step()

tensor(0.9787, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9787, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9786, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9786, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9786, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9785, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9785, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9784, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9783, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9783, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9782, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9781, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9780, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9780, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9779, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9778, grad_fn=<BinaryCrossEntropyWithLogitsBac

tensor(0.9549, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9548, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9547, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9546, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9544, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9543, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9542, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9541, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9540, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9539, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9538, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9537, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9536, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9535, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9533, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9532, grad_fn=<BinaryCrossEntropyWithLogitsBac

tensor(0.9394, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9393, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9392, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9391, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9389, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9388, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9387, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9386, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9385, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9384, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9383, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9382, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9381, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9380, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9379, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9377, grad_fn=<BinaryCrossEntropyWithLogitsBac

tensor(0.9226, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9225, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9224, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9223, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9222, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9221, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9220, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9218, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9217, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9216, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9215, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9214, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9213, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9212, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9211, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9210, grad_fn=<BinaryCrossEntropyWithLogitsBac

tensor(0.9051, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9050, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9049, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9048, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9047, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9046, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9045, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9044, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9043, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9042, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9041, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9040, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9039, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9038, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9037, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.9035, grad_fn=<BinaryCrossEntropyWithLogitsBac

...

tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBac

tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBac

tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBac

tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBackward>)
tensor(0.0008, grad_fn=<BinaryCrossEntropyWithLogitsBac

KeyboardInterrupt: 